In [1]:
import pandas as pd
import sweetviz as sv
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
#from ydata_profiling import ProfileReport
from sklearn.pipeline import Pipeline, make_pipeline
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import FunctionTransformer
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import LabelEncoder, OrdinalEncoder
from pandas.api.types import CategoricalDtype
from sklearn.model_selection import train_test_split

from sklearn.model_selection import GridSearchCV
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

from sklearn.linear_model import LinearRegression
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.neural_network import MLPRegressor
import joblib

In [2]:
# Charger le dataset
df = pd.read_csv('dataset_revenu_marocains.csv')

In [3]:
# Afficher les 10 premières instances
df.head(10)

Identifiant  Âge   Sexe Niveau d'éducation État matrimonial Urbain/Rural  \
0            1   56  Femme        fondamental      célibataire        Rural   
1            2   69  Homme        fondamental            marié       Urbain   
2            3   46  Homme        fondamental             veuf       Urbain   
3            4   32  Femme          supérieur      célibataire        Rural   
4            5   60  Femme        sans niveau            marié        Rural   
5            6   25  Homme        sans niveau      célibataire       Urbain   
6            7   38  Femme        fondamental      célibataire       Urbain   
7            8   56  Femme        sans niveau            marié        Rural   
8            9   36  Homme        fondamental            marié        Rural   
9           10   40  Homme          supérieur      célibataire       Urbain   

  Catégorie socioprofessionnelle  Années d'expérience Possession de biens  \
0                       Groupe 5                    7            Logement   
1                       Groupe 6                   10             Voiture   
2                       Groupe 2                   10             Voiture   
3                       Groupe 5                   34             Terrain   
4                       Groupe 4                   14               Aucun   
5                       Groupe 4                    7             Terrain   
6                       Groupe 2                   21            Logement   
7                       Groupe 2                   33               Aucun   
8                       Groupe 4                   39            Logement   
9                       Groupe 3                   45             Terrain   

                      Région Type de contrat Langue maternelle  \
0       Béni Mellal-Khénifra             CDI              arab   
1          Guelmim-Oued Noun             CDD              arab   
2          Guelmim-Oued Noun             CDD              arab   
3          Casablanca-Settat             CDI              arab   
4         Rabat-Salé-Kénitra    sans contrat              arab   
5    Laâyoune-Sakia El Hamra    sans contrat           amazigh   
6  Tanger-Tétouan-Al Hoceïma             CDD              arab   
7       Dakhla-Oued Ed-Dahab             CDD              arab   
8          Guelmim-Oued Noun    sans contrat           amazigh   
9             Marrakech-Safi    sans contrat              arab   

   Revenu annuel (DH)  Âge doublé  Revenu approximatif Code aléatoire  
0              7000.0         112              11000.0           Y456  
1             10282.0         138              17000.0           Z789  
2             34036.0          92              50000.0           W000  
3             14793.0          64              24000.0           W000  
4              9782.0         120              16000.0           W000  
5             14092.0          50              23000.0           X123  
6             34721.0          76              52000.0           X123  
7             26798.0         112              44000.0           Z789  
8             16359.0          72              27000.0           X123  
9             42492.0          80              64000.0           W000

In [6]:
# Afficher le volume (nombre d'instances) et la dimension (nombre d'attributs)
print(f"Volume (nombre d'instances) : {df.shape[0]}")
print(f"Dimension (nombre d'attributs) : {df.shape[1]}")

# Afficher les types et le codage des attributs
print("\nTypes des colonnes :")
df.info()


Volume (nombre d'instances) : 40000
Dimension (nombre d'attributs) : 16

Types des colonnes :
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 40000 entries, 0 to 39999
Data columns (total 16 columns):
 #   Column                          Non-Null Count  Dtype  
---  ------                          --------------  -----  
 0   Identifiant                     40000 non-null  int64  
 1   Âge                             40000 non-null  int64  
 2   Sexe                            40000 non-null  object 
 3   Niveau d'éducation              39200 non-null  object 
 4   État matrimonial                39200 non-null  object 
 5   Urbain/Rural                    40000 non-null  object 
 6   Catégorie socioprofessionnelle  40000 non-null  object 
 7   Années d'expérience             40000 non-null  int64  
 8   Possession de biens             40000 non-null  object 
 9   Région                          40000 non-null  object 
 10  Type de contrat                 40000 non-null  object 
 11 

In [7]:
df.describe(include='all')

Identifiant           Âge   Sexe Niveau d'éducation État matrimonial  \
count   40000.00000  40000.000000  40000              39200            39200   
unique          NaN           NaN      2                  4                4   
top             NaN           NaN  Femme        sans niveau            marié   
freq            NaN           NaN  20101              14112            22783   
mean    20000.50000     43.501325    NaN                NaN              NaN   
std     11547.14972     15.031071    NaN                NaN              NaN   
min         1.00000     -5.000000    NaN                NaN              NaN   
25%     10000.75000     31.000000    NaN                NaN              NaN   
50%     20000.50000     43.000000    NaN                NaN              NaN   
75%     30000.25000     56.000000    NaN                NaN              NaN   
max     40000.00000    150.000000    NaN                NaN              NaN   

       Urbain/Rural Catégorie socioprofessionnelle  Années d'expérience  \
count         40000                          40000         40000.000000   
unique            2                              6                  NaN   
top          Urbain                       Groupe 5                  NaN   
freq          23865                          10151                  NaN   
mean            NaN                            NaN            24.472125   
std             NaN                            NaN            14.478731   
min             NaN                            NaN             0.000000   
25%             NaN                            NaN            12.000000   
50%             NaN                            NaN            24.000000   
75%             NaN                            NaN            37.000000   
max             NaN                            NaN            49.000000   

       Possession de biens                Région Type de contrat  \
count                40000                 40000           40000   
unique                   4                    12               3   
top                Terrain  Béni Mellal-Khénifra             CDI   
freq                 10115                  3383           13416   
mean                   NaN                   NaN             NaN   
std                    NaN                   NaN             NaN   
min                    NaN                   NaN             NaN   
25%                    NaN                   NaN             NaN   
50%                    NaN                   NaN             NaN   
75%                    NaN                   NaN             NaN   
max                    NaN                   NaN             NaN   

       Langue maternelle  Revenu annuel (DH)    Âge doublé  \
count              39200        3.920000e+04  40000.000000   
unique                 2                 NaN           NaN   
top                 arab                 NaN           NaN   
freq               31742                 NaN           NaN   
mean                 NaN        2.263933e+04     87.002650   
std                  NaN        7.071816e+04     30.062142   
min                  NaN       -3.078000e+03    -10.000000   
25%                  NaN        1.223175e+04     62.000000   
50%                  NaN        1.741600e+04     86.000000   
75%                  NaN        2.665050e+04    112.000000   
max                  NaN        6.159536e+06    300.000000   

        Revenu approximatif Code aléatoire  
count          3.920000e+04          40000  
unique                  NaN              4  
top                     NaN           Z789  
freq                    NaN          10097  
mean           3.565316e+04            NaN  
std            1.145135e+05            NaN  
min           -5.000000e+03            NaN  
25%            2.000000e+04            NaN  
50%            2.800000e+04            NaN  
75%            4.200000e+04            NaN  
max            1.000000e+07            NaN

In [25]:
# Générer le rapport de profilage
rapport = ProfileReport(df, title="Profil du dataset", explorative=True)

# Afficher dans le notebook
rapport.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]


100%|██████████████████████████████████████████████████████████████████████████████████| 16/16 [00:01<00:00, 13.90it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [6]:
rapport.to_file("rapport_profiling.html")


Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [4]:
# Supprimer les doublons
df = df.drop_duplicates()


In [5]:
# Étape 1 — Supprimer les doublons
def remove_duplicates(X):
    return X.drop_duplicates()

# Étape 2 — Traiter les valeurs aberrantes
def handle_outliers(X):
    X = X.copy()
    X.loc[(X['Âge'] < 18) | (X['Âge'] > 100), 'Âge'] = np.nan
    X.loc[(X['Revenu annuel (DH)'] < 1000) | (X['Revenu annuel (DH)'] > 1_000_000), 'Revenu annuel (DH)'] = np.nan
    return X

# Étape 3 — Définir les colonnes
numerical_cols = ['Âge', 'Années d\'expérience', 'Revenu annuel (DH)']
categorical_cols = ['Sexe', 'Niveau d\'éducation', 'État matrimonial', 'Urbain/Rural',
                    'Catégorie socioprofessionnelle', 'Possession de biens',
                    'Région', 'Type de contrat', 'Langue maternelle']

# Étape 4 — Pipelines pour l'imputation
categorical_pipeline = make_pipeline(
    SimpleImputer(strategy='most_frequent')
)

numerical_pipeline = make_pipeline(
    SimpleImputer(strategy='median')
)

# Étape 5 — ColumnTransformer
preprocessor = ColumnTransformer(transformers=[
    ('num', numerical_pipeline, numerical_cols),
    ('cat', categorical_pipeline, categorical_cols)
])

# Étape 6 — Pipeline complet
cleaning_pipeline = Pipeline(steps=[
    ('remove_duplicates', FunctionTransformer(remove_duplicates)),
    ('handle_outliers', FunctionTransformer(handle_outliers)),
    ('imputer', preprocessor)
])

# Appliquer la transformation
X_clean = cleaning_pipeline.fit_transform(df)

# Convertir le résultat en DataFrame
clean_columns = numerical_cols + categorical_cols
X_clean_df = pd.DataFrame(X_clean, columns=clean_columns)



print("Données nettoyées (shape):", X_clean_df.shape)

# Sauvegarde dans un fichier CSV
X_clean_df.to_csv("dataset_nettoye.csv", index=False, encoding='utf-8-sig')

X_clean_df.head()

Données nettoyées (shape): (40000, 12)


Âge Années d'expérience Revenu annuel (DH)   Sexe Niveau d'éducation  \
0  56.0                 7.0             7000.0  Femme        fondamental   
1  69.0                10.0            10282.0  Homme        fondamental   
2  46.0                10.0            34036.0  Homme        fondamental   
3  32.0                34.0            14793.0  Femme          supérieur   
4  60.0                14.0             9782.0  Femme        sans niveau   

  État matrimonial Urbain/Rural Catégorie socioprofessionnelle  \
0      célibataire        Rural                       Groupe 5   
1            marié       Urbain                       Groupe 6   
2             veuf       Urbain                       Groupe 2   
3      célibataire        Rural                       Groupe 5   
4            marié        Rural                       Groupe 4   

  Possession de biens                Région Type de contrat Langue maternelle  
0            Logement  Béni Mellal-Khénifra             CDI              arab  
1             Voiture     Guelmim-Oued Noun             CDD              arab  
2             Voiture     Guelmim-Oued Noun             CDD              arab  
3             Terrain     Casablanca-Settat             CDI              arab  
4               Aucun    Rabat-Salé-Kénitra    sans contrat              arab

In [6]:
X_transformed = X_clean_df.copy()

In [7]:
# Normalisation
X_normalisationNumeric=X_transformed.copy()
scaler = StandardScaler()
numerical_cols_transformed =['Âge', 'Années d\'expérience', 'Revenu annuel (DH)']
X_normalisationNumeric[numerical_cols_transformed] = scaler.fit_transform(X_normalisationNumeric[numerical_cols_transformed])

print("✅ Normalisation effectuée")
X_normalisationNumeric.to_csv("dataset_transformation_numerique.csv", index=False, encoding='utf-8-sig')
display(X_normalisationNumeric.head())

✅ Normalisation effectuée


Âge  Années d'expérience  Revenu annuel (DH)   Sexe  \
0  0.835194            -1.206759           -1.061631  Femme   
1  1.703375            -0.999556           -0.825724  Homme   
2  0.167362            -0.999556            0.881688  Homme   
3 -0.767602             0.658068           -0.501479  Femme   
4  1.102326            -0.723285           -0.861664  Femme   

  Niveau d'éducation État matrimonial Urbain/Rural  \
0        fondamental      célibataire        Rural   
1        fondamental            marié       Urbain   
2        fondamental             veuf       Urbain   
3          supérieur      célibataire        Rural   
4        sans niveau            marié        Rural   

  Catégorie socioprofessionnelle Possession de biens                Région  \
0                       Groupe 5            Logement  Béni Mellal-Khénifra   
1                       Groupe 6             Voiture     Guelmim-Oued Noun   
2                       Groupe 2             Voiture     Guelmim-Oued Noun   
3                       Groupe 5             Terrain     Casablanca-Settat   
4                       Groupe 4               Aucun    Rabat-Salé-Kénitra   

  Type de contrat Langue maternelle  
0             CDI              arab  
1             CDD              arab  
2             CDD              arab  
3             CDI              arab  
4    sans contrat              arab

In [9]:

# Copie pour transformation catégoriale
df_encoded = X_transformed.copy()

# 1. Encodage ordinal pour niveau d'éducation
edu_order = CategoricalDtype(categories=['sans niveau', 'fondamental', 'secondaire', 'supérieur'], ordered=True)
df_encoded['Niveau d\'éducation'] = df_encoded['Niveau d\'éducation'].astype(edu_order)
df_encoded['Niveau d\'éducation'] = df_encoded['Niveau d\'éducation'].cat.codes

# 2. Label Encoding pour les colonnes binaires
label_cols = ['Sexe', 'Urbain/Rural', 'Langue maternelle']
le = LabelEncoder()
for col in label_cols:
    df_encoded[col] = le.fit_transform(df_encoded[col])

# 3. One-hot encoding pour colonnes nominales
one_hot_cols = ['État matrimonial', 'Possession de biens', 'Région', 'Type de contrat']
df_encoded = pd.get_dummies(df_encoded, columns=one_hot_cols, drop_first=False)


# 4. Label Encoding pour la catégorie socioprofessionnelle (simplifié)
df_encoded['Catégorie socioprofessionnelle'] = le.fit_transform(df_encoded['Catégorie socioprofessionnelle'].astype(str))
df_encoded.to_csv("dataset_transformation_categorial.csv", index=False, encoding='utf-8-sig')
df_encoded.head()


Âge Années d'expérience Revenu annuel (DH)  Sexe  Niveau d'éducation  \
0  56.0                 7.0             7000.0     0                   1   
1  69.0                10.0            10282.0     1                   1   
2  46.0                10.0            34036.0     1                   1   
3  32.0                34.0            14793.0     0                   3   
4  60.0                14.0             9782.0     0                   0   

   Urbain/Rural  Catégorie socioprofessionnelle  Langue maternelle  \
0             0                               4                  1   
1             1                               5                  1   
2             1                               1                  1   
3             0                               4                  1   
4             0                               3                  1   

   État matrimonial_célibataire  État matrimonial_divorcé  ...  \
0                          True                     False  ...   
1                         False                     False  ...   
2                         False                     False  ...   
3                          True                     False  ...   
4                         False                     False  ...   

   Région_Guelmim-Oued Noun  Région_Laâyoune-Sakia El Hamra  \
0                     False                           False   
1                      True                           False   
2                      True                           False   
3                     False                           False   
4                     False                           False   

   Région_L’Oriental  Région_Marrakech-Safi  Région_Rabat-Salé-Kénitra  \
0              False                  False                      False   
1              False                  False                      False   
2              False                  False                      False   
3              False                  False                      False   
4              False                  False                       True   

   Région_Souss-Massa  Région_Tanger-Tétouan-Al Hoceïma  Type de contrat_CDD  \
0               False                             False                False   
1               False                             False                 True   
2               False                             False                 True   
3               False                             False                False   
4               False                             False                False   

   Type de contrat_CDI  Type de contrat_sans contrat  
0                 True                         False  
1                False                         False  
2                False                         False  
3                 True                         False  
4                False                          True  

[5 rows x 31 columns]

In [10]:
# Supposons que df_encoded est déjà nettoyé et les colonnes ctégoriales sont transformé
train_set, test_set = train_test_split(df_encoded, test_size=0.3, random_state=42)

train_set.to_csv("dataset_initial_70.csv", index=False, encoding='utf-8-sig')
test_set.to_csv("dataset_initial_30.csv", index=False, encoding='utf-8-sig')
# Affichage des dimensions
print(f"Taille ensemble d'apprentissage : {train_set.shape}")
print(f"Taille ensemble de test        : {test_set.shape}")

Taille ensemble d'apprentissage : (28000, 31)
Taille ensemble de test        : (12000, 31)


In [11]:
X_train = train_set.drop("Revenu annuel (DH)", axis=1)  #le nom de ta variable cible est revenue annuel
y_train = train_set["Revenu annuel (DH)"]

X_test = test_set.drop("Revenu annuel (DH)", axis=1)
y_test = test_set["Revenu annuel (DH)"]

In [12]:

model = LinearRegression()
model.fit(X_train, y_train)
y_pred_linear = model.predict(X_test)

print("Régression Linéaire")
print("MAE :", mean_absolute_error(y_test, y_pred_linear))
print("RMSE:", np.sqrt(mean_squared_error(y_test, y_pred_linear)))
print("R²  :", r2_score(y_test, y_pred_linear))


Régression Linéaire
MAE : 4425.447265493747
RMSE: 6026.704502873451
R²  : 0.8031118445230705


In [13]:
params = {
    'criterion': ['squared_error', 'absolute_error'],
    'max_depth': [None, 5, 6, 7, 10],
    'min_samples_split': [2, 3, 4, 5, 10]
}

grid_tree = GridSearchCV(DecisionTreeRegressor(), params, cv=5, scoring='neg_mean_squared_error', n_jobs=-1)
grid_tree.fit(X_train, y_train)
y_pred_tree = grid_tree.best_estimator_.predict(X_test)

print("Decision Tree")
print("Best Params:", grid_tree.best_params_)
print("MAE :", mean_absolute_error(y_test, y_pred_tree))
print("RMSE:", np.sqrt(mean_squared_error(y_test, y_pred_tree)))
print("R²  :", r2_score(y_test, y_pred_tree))


Decision Tree
Best Params: {'criterion': 'squared_error', 'max_depth': None, 'min_samples_split': 5}
MAE : 1410.0460555555553
RMSE: 3593.798137451357
R²  : 0.9299888594229


In [14]:
#Gradiant boosting
params = {
    'loss': ['squared_error', 'absolute_error'],
    'learning_rate': [0.01, 0.1, 0.2],
    'n_estimators': [100, 200, 300],
    'subsample': [0.5, 0.8, 1]
}

grid = GridSearchCV(GradientBoostingRegressor(), params, cv=5, scoring='neg_mean_squared_error', n_jobs=-1)
grid.fit(X_train, y_train)
y_pred = grid.best_estimator_.predict(X_test)

print("Gradient Boosting")
print("Best Params:", grid.best_params_)
print("MAE :", mean_absolute_error(y_test, y_pred))
print("RMSE:", np.sqrt(mean_squared_error(y_test, y_pred)))
print("R²  :", r2_score(y_test, y_pred))

Gradient Boosting
Best Params: {'learning_rate': 0.2, 'loss': 'squared_error', 'n_estimators': 300, 'subsample': 1}
MAE : 1005.6176075935906
RMSE: 3385.976411230603
R²  : 0.9378519293360026


In [ ]:
#random forest
params = {
    'n_estimators': [50, 100, 150, 200],
    'criterion': ['squared_error', 'absolute_error'],
    'max_depth': [None, 5, 10, 15, 20]
}

grid = GridSearchCV(RandomForestRegressor(), params, cv=5, scoring='neg_mean_squared_error', n_jobs=-1)
grid.fit(X_train, y_train)
y_pred = grid.best_estimator_.predict(X_test)

print("Random Forest")
print("Best Params:", grid.best_params_)
print("MAE :", mean_absolute_error(y_test, y_pred))
print("RMSE:", np.sqrt(mean_squared_error(y_test, y_pred)))
print("R²  :", r2_score(y_test, y_pred))


In [ ]:
params = {
    'hidden_layer_sizes': [(50,), (100,), (100, 50), (100, 100)],
    'activation': ['relu', 'tanh', 'logistic'],
    'solver': ['adam', 'sgd'],
    'alpha': [0.0001, 0.001, 0.01],
    'learning_rate': ['constant', 'invscaling', 'adaptive'],
    'learning_rate_init': [0.001, 0.01, 0.1],
    'max_iter': [100, 200, 300]
}

grid = GridSearchCV(MLPRegressor(), params, cv=3, scoring='neg_mean_squared_error', n_jobs=-1)
grid.fit(X_train, y_train)
y_pred = grid.best_estimator_.predict(X_test)

print("MLP Regressor")
print("Best Params:", grid.best_params_)
print("MAE :", mean_absolute_error(y_test, y_pred))
print("RMSE:", np.sqrt(mean_squared_error(y_test, y_pred)))
print("R²  :", r2_score(y_test, y_pred))

In [15]:
joblib.dump(grid.best_estimator_, "modele_selection.joblib")

['modele_selection.joblib']

In [16]:
#Verification du chargement du modèle
model_loaded = joblib.load("modele_selection.joblib")

# Faire une prédiction avec le modèle chargé (par exemple sur X_test)
y_pred = model_loaded.predict(X_test)

print("Prédiction avec le modèle chargé :", y_pred[:5])  # Affiche les 5 premières prédictions

Prédiction avec le modèle chargé : [23958.5336288  22576.20367655 23214.91298652 11183.27444086
 16496.74605928]


In [17]:
print(df_encoded.columns.tolist())
print(len(df_encoded.columns))  # ← doit être 30


['Âge', "Années d'expérience", 'Revenu annuel (DH)', 'Sexe', "Niveau d'éducation", 'Urbain/Rural', 'Catégorie socioprofessionnelle', 'Langue maternelle', 'État matrimonial_célibataire', 'État matrimonial_divorcé', 'État matrimonial_marié', 'État matrimonial_veuf', 'Possession de biens_Aucun', 'Possession de biens_Logement', 'Possession de biens_Terrain', 'Possession de biens_Voiture', 'Région_Béni Mellal-Khénifra', 'Région_Casablanca-Settat', 'Région_Dakhla-Oued Ed-Dahab', 'Région_Drâa-Tafilalet', 'Région_Fès-Meknès', 'Région_Guelmim-Oued Noun', 'Région_Laâyoune-Sakia El Hamra', 'Région_L’Oriental', 'Région_Marrakech-Safi', 'Région_Rabat-Salé-Kénitra', 'Région_Souss-Massa', 'Région_Tanger-Tétouan-Al Hoceïma', 'Type de contrat_CDD', 'Type de contrat_CDI', 'Type de contrat_sans contrat']
31
